In [3]:
import sys
import copy

BOARD_SIZE = 8
REGULAR_VALUE = 1
KING_VALUE = 2

RED_DIRECTIONS = [(1, -1), (1, 1)]
BLACK_DIRECTIONS = [(-1, -1), (-1, 1)]
KING_DIRECTIONS = RED_DIRECTIONS + BLACK_DIRECTIONS

class Checkers:
    def __init__(self):
        self.board = [[None for _ in range(BOARD_SIZE)] for _ in range(BOARD_SIZE)]
        self.create_board()
        self.current_player = 'r'

    def create_board(self):
        for row in range(BOARD_SIZE):
            for col in range(BOARD_SIZE):
                if (row + col) % 2 == 0:
                    if row < 3:
                        self.board[row][col] = 'r'
                    elif row > 4:
                        self.board[row][col] = 'b'
                    else:
                        self.board[row][col] = '.'
                else:
                    self.board[row][col] = ' '

    def print_board(self):
        print("  " + " ".join(map(str, range(BOARD_SIZE))))
        for i, row in enumerate(self.board):
            print(i, end=" ")
            for cell in row:
                print(cell if cell is not None else '.', end=" ")
            print()
        print()

    def get_all_valid_moves(self, player):
        moves = []
        captures = []
        for row in range(BOARD_SIZE):
            for col in range(BOARD_SIZE):
                piece = self.board[row][col]
                if piece is None or piece == '.' or piece == ' ':
                    continue
                if player == 'r' and piece.lower() == 'r':
                    m, c = self.get_valid_moves_for_piece(row, col)
                    moves.extend(m)
                    captures.extend(c)
                elif player == 'b' and piece.lower() == 'b':
                    m, c = self.get_valid_moves_for_piece(row, col)
                    moves.extend(m)
                    captures.extend(c)
        return captures if captures else moves

    def get_valid_moves_for_piece(self, row, col):
        moves = []
        captures = []
        piece = self.board[row][col]
        if piece is None or piece == '.' or piece == ' ':
            return moves, captures

        if piece == 'r':
            directions = RED_DIRECTIONS
            enemy = ['b', 'B']
        elif piece == 'b':
            directions = BLACK_DIRECTIONS
            enemy = ['r', 'R']
        else:
            directions = KING_DIRECTIONS
            enemy = ['b', 'B'] if piece.upper() == 'R' else ['r', 'R']

        for dr, dc in directions:
            new_r, new_c = row + dr, col + dc
            if 0 <= new_r < BOARD_SIZE and 0 <= new_c < BOARD_SIZE:
                if self.board[new_r][new_c] == '.':
                    moves.append((row, col, new_r, new_c))
            cap_r, cap_c = row + 2 * dr, col + 2 * dc
            if 0 <= cap_r < BOARD_SIZE and 0 <= cap_c < BOARD_SIZE:
                mid_r, mid_c = row + dr, col + dc
                if self.board[mid_r][mid_c] in enemy and self.board[cap_r][cap_c] == '.':
                    captures.append((row, col, cap_r, cap_c))
        return moves, captures

    def make_move(self, move, player):
        sr, sc, er, ec = move
        piece = self.board[sr][sc]
        self.board[er][ec] = piece
        self.board[sr][sc] = '.'

        if abs(er - sr) == 2:
            self.board[(sr + er) // 2][(sc + ec) // 2] = '.'

        if piece == 'r' and er == BOARD_SIZE - 1:
            self.board[er][ec] = 'R'
        elif piece == 'b' and er == 0:
            self.board[er][ec] = 'B'

    def is_game_over(self):
        red_exists = any(self.board[r][c] is not None and self.board[r][c].lower() == 'r'
                         for r in range(BOARD_SIZE) for c in range(BOARD_SIZE))
        black_exists = any(self.board[r][c] is not None and self.board[r][c].lower() == 'b'
                           for r in range(BOARD_SIZE) for c in range(BOARD_SIZE))
        if not red_exists or not black_exists:
            return True
        if not self.get_all_valid_moves(self.current_player):
            return True
        return False

    def evaluate(self):
        red_score = 0
        black_score = 0
        for row in range(BOARD_SIZE):
            for col in range(BOARD_SIZE):
                piece = self.board[row][col]
                if piece == 'r':
                    red_score += REGULAR_VALUE
                elif piece == 'R':
                    red_score += KING_VALUE
                elif piece == 'b':
                    black_score += REGULAR_VALUE
                elif piece == 'B':
                    black_score += KING_VALUE
        return black_score - red_score

    def alphabeta(self, depth, alpha, beta, maximizing_player):
        if depth == 0 or self.is_game_over():
            return self.evaluate(), None

        current = 'b' if maximizing_player else 'r'
        valid_moves = self.get_all_valid_moves(current)
        best_move = None

        if maximizing_player:
            max_eval = -float("inf")
            for move in valid_moves:
                new_game = copy.deepcopy(self)
                new_game.make_move(move, current)
                new_game.current_player = 'r'
                eval_score, _ = new_game.alphabeta(depth - 1, alpha, beta, False)
                if eval_score > max_eval:
                    max_eval = eval_score
                    best_move = move
                alpha = max(alpha, eval_score)
                if beta <= alpha:
                    break
            return max_eval, best_move
        else:
            min_eval = float("inf")
            for move in valid_moves:
                new_game = copy.deepcopy(self)
                new_game.make_move(move, current)
                new_game.current_player = 'b'
                eval_score, _ = new_game.alphabeta(depth - 1, alpha, beta, True)
                if eval_score < min_eval:
                    min_eval = eval_score
                    best_move = move
                beta = min(beta, eval_score)
                if beta <= alpha:
                    break
            return min_eval, best_move


def play_human_vs_ai():
    game = Checkers()
    print("Welcome to Checkers! You are Red ('r'). AI is Black ('b').")
    game.print_board()

    while not game.is_game_over():
        if game.current_player == 'r':
            print("Your turn (Red).")
            moves = game.get_all_valid_moves('r')
            if not moves:
                break
            print("Valid moves:")
            for idx, move in enumerate(moves):
                print(f"{idx}: from ({move[0]}, {move[1]}) to ({move[2]}, {move[3]})")
            choice = input("Enter move number (or 'q' to quit): ").strip().lower()
            if choice == 'q':
                print("Exiting game.")
                break
            if not choice.isdigit() or int(choice) < 0 or int(choice) >= len(moves):
                print("Invalid input. Try again.")
                continue
            move = moves[int(choice)]
            game.make_move(move, 'r')
            game.current_player = 'b'
        else:
            print("AI's turn (Black)...")
            _, best_move = game.alphabeta(4, -float("inf"), float("inf"), True)
            if best_move is None:
                print("AI has no valid moves.")
                break
            print(f"AI moves from ({best_move[0]}, {best_move[1]}) to ({best_move[2]}, {best_move[3]})")
            game.make_move(best_move, 'b')
            game.current_player = 'r'
        game.print_board()

    print("Game Over.")
    final_eval = game.evaluate()
    if final_eval > 0:
        print("AI (Black) wins!")
    elif final_eval < 0:
        print("You (Red) win!")
    else:
        print("It's a draw!")


def play_ai_vs_ai():
    game = Checkers()
    print("Starting AI vs AI game (Black vs Red).")
    game.print_board()

    while not game.is_game_over():
        current = game.current_player
        print(f"AI ({'Black' if current == 'b' else 'Red'}) is thinking...")
        _, best_move = game.alphabeta(
            depth=4,
            alpha=-float("inf"),
            beta=float("inf"),
            maximizing_player=(current == 'b')
        )

        if best_move is None:
            print(f"AI ({current}) has no valid moves.")
            break

        print(f"AI ({current}) moves from ({best_move[0]}, {best_move[1]}) to ({best_move[2]}, {best_move[3]})")
        game.make_move(best_move, current)
        game.current_player = 'b' if current == 'r' else 'r'
        game.print_board()

    print("Game Over.")
    final_eval = game.evaluate()
    if final_eval > 0:
        print("AI Black wins!")
    elif final_eval < 0:
        print("AI Red wins!")
    else:
        print("It's a draw!")


if __name__ == "__main__":
    print("Select game mode:")
    print("1: Human vs AI")
    print("2: AI vs AI")
    mode = input("Enter 1 or 2: ").strip()

    if mode == '1':
        play_human_vs_ai()
    elif mode == '2':
        play_ai_vs_ai()
    else:
        print("Invalid mode selected.")


Select game mode:
1: Human vs AI
2: AI vs AI
Starting AI vs AI game (Black vs Red).
  0 1 2 3 4 5 6 7
0 r   r   r   r   
1   r   r   r   r 
2 r   r   r   r   
3   .   .   .   . 
4 .   .   .   .   
5   b   b   b   b 
6 b   b   b   b   
7   b   b   b   b 

AI (Red) is thinking...
AI (r) moves from (2, 0) to (3, 1)
  0 1 2 3 4 5 6 7
0 r   r   r   r   
1   r   r   r   r 
2 .   r   r   r   
3   r   .   .   . 
4 .   .   .   .   
5   b   b   b   b 
6 b   b   b   b   
7   b   b   b   b 

AI (Black) is thinking...
AI (b) moves from (5, 1) to (4, 0)
  0 1 2 3 4 5 6 7
0 r   r   r   r   
1   r   r   r   r 
2 .   r   r   r   
3   r   .   .   . 
4 b   .   .   .   
5   .   b   b   b 
6 b   b   b   b   
7   b   b   b   b 

AI (Red) is thinking...
AI (r) moves from (1, 1) to (2, 0)
  0 1 2 3 4 5 6 7
0 r   r   r   r   
1   .   r   r   r 
2 r   r   r   r   
3   r   .   .   . 
4 b   .   .   .   
5   .   b   b   b 
6 b   b   b   b   
7   b   b   b   b 

AI (Black) is thinking...
AI (b) moves from (5, 3) to

KeyboardInterrupt: 

In [ ]:
import sys
import copy
BOARD_SIZE = 8
class Checkers:
    def __init__(self):
        pass
    def create_board(self):
        """
        Set up the initial 8x8 board:
        - Red pieces on top 3 rows, black pieces on bottom 3 rows.
        - Only place pieces on dark squares ((row + col) % 2 == 0).
        """
        pass
    def print_board(self):
        """
        Display the current board with row and column numbers.
        """
        pass
    def get_all_valid_moves(self, player):
        """
        Return a list of all valid moves for the given player ('r' or 'b').
        Include moves for regular and king pieces, and prioritize captures.
        """
        pass
    def get_valid_moves_for_piece(self, row, col):
        """
        Given a piece's position, return all valid move options for that piece.
        Account for direction (forward for regular, both for king) and captures.
        """
        pass
    def make_move(self, move, player):

        """
        Apply the move to the board:
        - Move the piece
        - Remove any captured opponent piece
        - Promote to king if piece reaches the last row
        """
        pass
    def is_game_over(self):
        """
        Check whether the game is over (no moves or no pieces for a player).
        """
        pass
    def evaluate(self):
        """
        Calculate board score: (1 × regular pieces) + (2 × kings).
        Return (AI's score - Opponent's score) to guide AI decisions.
        """
        pass
    def alphabeta(self, depth, alpha, beta, maximizing_player):
        """
        Use Minimax with Alpha-Beta Pruning to select the best move.
        """
        pass
    def play_human_vs_ai():
        """
        Launch a human vs AI game of Checkers in the console.
        AI (Black) uses Alpha-Beta Pruning; human plays as Red.
        Display board, show legal moves, and accept input for human turns.
        """
        pass
    # Entry point
if __name__ == "__main__":
play_human_vs_ai()